# Creating Bangalore Grid

Here, we will create a hexagonal grid of uniform size to cover the Bangalore city area. We will use data from the [Karanataka Government website](https://kgis.ksrsac.in/kgis/downloads.aspx)  (converted to GeoJSON [here](https://ogre.adc4gis.com/)), which has been retrieved and stored in the data folder.

In [1]:
import numpy as np

from geopy import Nominatim

from ratelimiter import RateLimiter
from diskcache import Cache

import geojson
import geopandas as gpd
from shapely.geometry.polygon import orient

import folium
import h3

In [2]:
# Creating a geocoder with specific user agent as required by Nominatim
geocoder = Nominatim(user_agent = 'coursera_capstone')

# Rate limiter to adhere to Nominatim's 1 request/second limit
limiter = RateLimiter(max_calls = 1, period = 1)

# Cache Path to store Nominatum responses
nom_cache = '../data/cache/nominatim'

## Obtain City Boundaries

We will use the ward map from the BBMP (Bangalore Municipal Corporation) for this project. The GeoJSON file was obtained from [this Github repository](https://github.com/datameet/Municipal_Spatial_Data).

The additional population data included in this dataset is from the 2011 Indian Census.

In [3]:
wardmap = '../data/BBMP.GeoJSON' # Data file path

# Obtain centre coordinates for map
map_centre_address = 'Bengaluru, Karnataka, India'

with Cache(nom_cache) as cache:
    map_centre = cache.get(map_centre_address) # Check for cached location before querying

    while not map_centre:
        with limiter:
            map_centre = geocoder.geocode(map_centre_address)
            cache.set(map_centre_address, map_centre) # Save to cache

# Plot map
bbmp_map = folium.Map((map_centre.latitude, map_centre.longitude), zoom_start=11)
folium.Choropleth(wardmap, name='geoJSON').add_to(bbmp_map)

bbmp_map # Display Map

### Data Cleaning

We will load the data into a GeoPandas GeoDataFrame for cleaning.

In [4]:
# Read the data into a GeoDataFrame
df_raw = gpd.read_file(wardmap)

df_raw.columns = df_raw.columns.str.lower() # Convert all columns to lowercase for consistency

print(df_raw.crs) # Check Coordinate Reference System
print(df_raw.columns) # Display list of columns

epsg:4326
Index(['objectid', 'ass_const_', 'ass_const1', 'ward_no', 'ward_name', 'pop_m',
       'pop_f', 'pop_sc', 'pop_st', 'pop_total', 'area_sq_km', 'lat', 'lon',
       'reservatio', 'geometry'],
      dtype='object')


In [5]:
# Keep only parameters of interest to us
df_wards = df_raw[[
    'geometry',
    'ward_no',
    'ward_name',
    'pop_total',
    'area_sq_km',
    'lat',
    'lon',
]].astype({'ward_no': 'int', 'pop_total': 'int'})

df_wards = df_wards.sort_values('ward_no').reset_index(drop=True)

bbmp_clean = '../data/BBMP_wards.geojson'
df_wards.to_file(bbmp_clean, driver='GeoJSON') # Persist cleaned data to file

#View cleaned data
print(df_wards.shape)
df_wards.head()

(198, 7)


geometry  ward_no  \
0  MULTIPOLYGON (((77.61515 13.13117, 77.61494 13...        1   
1  MULTIPOLYGON (((77.59229 13.09720, 77.59094 13...        2   
2  MULTIPOLYGON (((77.56862 13.12705, 77.57064 13...        3   
3  MULTIPOLYGON (((77.59094 13.09842, 77.59229 13...        4   
4  MULTIPOLYGON (((77.64650 13.08523, 77.64514 13...        5   

                  ward_name  pop_total  area_sq_km        lat        lon  
0           Kempegowda Ward      21866       10.47  13.116188  77.599713  
1          Chowdeswari Ward      19626        7.06  13.121709  77.580422  
2                    Atturu      24020       10.15  13.102805  77.560038  
3  Yelahanka Satellite Town      25782        4.90  13.090987  77.583925  
4                   Jakkuru      20964       23.96  13.096250  77.623314

The geometry is in the form of multipolygons, the H3 functions require polygons. We can convert each multipolygon to a list of polygons and iterate over the table collecting all polygons. We also need to ensure all polygons are oriented correctly according to the right hand rule.

In [6]:
polygons = [] # Create list to hold all polygons in the dataset
polygon_ward_no = [] # Record which ward number each polygon belongs to

for i, g in zip(df_wards['ward_no'], df_wards.geometry):
    multipolygon = list(g)
    for polygon in multipolygon:
        polygons.append(orient(polygon)) # Correct orientation before adding to list
        polygon_ward_no.append(i)

print('{} polygons extracted.'.format(len(polygons)))

204 polygons extracted.


## Creating Hexagonal grid

We wil use the [H3](https://github.com/uber/h3) geospatial system developed by Uber to create a grid of hex tiles covering the area described by our geoJSON file.

Below is the table of possible resolutions, taken from [link](https://h3geo.org/docs/core-library/restable).

| H3 Resolution | Average Hexagon Area (km<sup>2</sup>) | Average Hexagon Edge Length (km) | Number of unique indexes |
|---------------|----------------------------|----------------------------------|--------------------------|
| 0             | 4,250,546.8477000          | 1,107.712591000                  | 122                      |
| 1             | 607,220.9782429            | 418.676005500                    | 842                      |
| 2             | 86,745.8540347             | 158.244655800                    | 5,882                    |
| 3             | 12,392.2648621             | 59.810857940                     | 41,162                   |
| 4             | 1,770.3235517              | 22.606379400                     | 288,122                  |
| 5             | 252.9033645                | 8.544408276                      | 2,016,842                |
| 6             | 36.1290521                 | 3.229482772                      | 14,117,882               |
| 7             | 5.1612932                  | 1.220629759                      | 98,825,162               |
| 8             | 0.7373276                  | 0.461354684                      | 691,776,122              |
| 9             | 0.1053325                  | 0.174375668                      | 4,842,432,842            |
| 10            | 0.0150475                  | 0.065907807                      | 33,897,029,882           |
| 11            | 0.0021496                  | 0.024910561                      | 237,279,209,162          |
| 12            | 0.0003071                  | 0.009415526                      | 1,660,954,464,122        |
| 13            | 0.0000439                  | 0.003559893                      | 11,626,681,248,842       |
| 14            | 0.0000063                  | 0.001348575                      | 81,386,768,741,882       |
| 15            | 0.0000009                  | 0.000509713                      | 569,707,381,193,162      |

In [7]:
hex_res = 8 # Set hex resolution to 8
hexagons = [] # Empty list to store hexes
hexagon_ward_no = []

for polygon, ward in zip(polygons, polygon_ward_no):
    area = eval(geojson.dumps(polygon)) # Convert to GeoJSON formatted string
    hex_set = list(h3.polyfill(area, hex_res, geo_json_conformant=True))
    for h in hex_set:
        hexagons.append(h)
        hexagon_ward_no.append(ward)

print('{} Hexagon Grid generated.'.format(len(hexagons)))

942 Hexagon Grid generated.


In [8]:
features_list = []

for hexagon, ward in zip(hexagons, hexagon_ward_no):
    hex_coords = list(h3.h3_to_geo_boundary(hexagon, geo_json = True))
    
    feature = geojson.Feature(
        geometry = geojson.Polygon([hex_coords]),
        id = hexagon,
        properties = {
            "ward_no": ward,
            "centre_lat": h3.h3_to_geo(hexagon)[0],
            "centre_lon": h3.h3_to_geo(hexagon)[1],
            "resolution": hex_res,
            },
    )
    features_list.append(feature)

hex_data = geojson.FeatureCollection(features_list)

## Plotting the grid

Check the grid before saving it.

In [9]:
# Plot map
hex_map = folium.Map((map_centre.latitude, map_centre.longitude), zoom_start=11)

# Draw Bangalore boundary area
folium.Choropleth(
    bbmp_clean,
    name='boundary',
    line_color = 'black',
    line_opacity = 0.8,
    line_weight = 2,
    fill_color = 'blue',
    fill_opacity = 0.0,
).add_to(hex_map)

# Draw hexes
folium.Choropleth(
    hex_data,
    name='hex-grid',
    line_color = 'blue',
    line_opacity = 0.9,
    line_weight = 1,
    fill_color = 'blue',
    fill_opacity = 0.2,
).add_to(hex_map)

hex_map # Display map

In [10]:
# Save file to GeoJSON
with open('../data/BBMP_hex.geojson', 'w') as outfile:
    geojson.dump(hex_data, outfile)